In [1]:
import pandas as pd
from functions import assembleDf, epochG, epochsG
from datetime import datetime, timedelta
import numpy as np
import sys
sys.path.append('..')
from pyglicko2.glicko2_tests import exampleCase
from pyglicko2.glicko2 import Player
import glicko2
import time


In [2]:
matches = pd.read_csv('../Data/matches_glicko2.csv',parse_dates = ['tourney_date'], 
                      infer_datetime_format = True)

Because memory constraints limit the batch size in epochsG, I will need to process incrementally.

In [3]:
# base batches.  can be further broken up by splitBatch
eg_batches_50 = [(s,f) for s,f in zip(range(0, 876_978-50_000,50_000),
                      range(50_000, 876978,50_000))] + [(850_000,876979)]
eg_batches_100 = [(s,f) for s,f in zip(range(0, 876_978-100_000,100_000),
                      range(100_000, 876978,100_000))] + [(800_000,876979)]

ratings_histories = []
players_dict = {}

In [4]:
def ceildiv(a, b):
    return -(a // -b)

In [5]:
def splitBatch(atuple, divisions):
    '''Break up batches into smaller pieces to allow epochsG to run.'''
    batch_size = ceildiv((atuple[1] - atuple[0]),divisions)
    if batch_size < (atuple[1] - atuple[0]):
        batches = [b for b in zip(range(atuple[0],atuple[1]-batch_size,batch_size),
             range(atuple[0]+batch_size,atuple[1],batch_size))]
        extra = [(batches[-1][1],atuple[1])]
        return batches + extra
    else:
        return atuple

In [6]:
%%time
for batch in eg_batches_50[0:1]:
    players_dict,rh = epochsG(matches[batch[0]:batch[1]],players_dict,365)
    ratings_histories += [rh]

CPU times: user 10.6 s, sys: 55.1 ms, total: 10.6 s
Wall time: 10.6 s


In [7]:
%%time

for batch in eg_batches_50[1:2]:
    players_dict,rh = epochsG(matches[batch[0]:batch[1]],players_dict,365)
    ratings_histories += [rh]

CPU times: user 4.01 s, sys: 36 ms, total: 4.05 s
Wall time: 4.03 s


In [8]:
%%time

for batch in eg_batches_50[2:3]:
    players_dict,rh = epochsG(matches[batch[0]:batch[1]],players_dict,365)
    ratings_histories += [rh]

CPU times: user 4.14 s, sys: 31.9 ms, total: 4.18 s
Wall time: 4.16 s


In [9]:
eg_batches_50[3]

(150000, 200000)

In [10]:
b = splitBatch(eg_batches_50[3],2); b0 = b[0]; b1 = b[1]
b

[(150000, 175000), (175000, 200000)]

In [11]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.97 s, sys: 12.4 ms, total: 1.98 s
Wall time: 1.98 s


In [12]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.94 s, sys: 10.7 ms, total: 1.95 s
Wall time: 1.95 s


In [13]:
splitBatch(eg_batches_50[4],3)

[(200000, 216667), (216667, 233334), (233334, 250000)]

In [14]:
b = splitBatch(eg_batches_50[4],4); 
b0 = b[0]; b1 = b[1]; b2 = b[2]; b3=b[3]
b

[(200000, 212500), (212500, 225000), (225000, 237500), (237500, 250000)]

In [15]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.06 s, sys: 7.94 ms, total: 1.07 s
Wall time: 1.07 s


In [16]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1 s, sys: 5.85 ms, total: 1.01 s
Wall time: 1.01 s


In [17]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.06 s, sys: 8 ms, total: 1.06 s
Wall time: 1.06 s


In [18]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.11 s, sys: 8.28 ms, total: 1.12 s
Wall time: 1.12 s


In [19]:
%%time
players_dict,rh = epochsG(matches[eg_batches_50[5][0]:eg_batches_50[5][1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 3.76 s, sys: 10.8 ms, total: 3.77 s
Wall time: 3.77 s


%%time
players_dict,rh = epochsG(matches[eg_batches_50[6][0]:eg_batches_50[6][1]],players_dict,365)
ratings_histories += [rh]

In [20]:
b = splitBatch(eg_batches_50[6],8); 
b0 = b[0]; b1 = b[1]; b2 = b[2]; b3=b[3];
b4 = b[0]; b5 = b[1]; b6 = b[2]; b7=b[3]
b

[(300000, 306250),
 (306250, 312500),
 (312500, 318750),
 (318750, 325000),
 (325000, 331250),
 (331250, 337500),
 (337500, 343750),
 (343750, 350000)]

In [21]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 807 ms, sys: 6.03 ms, total: 813 ms
Wall time: 810 ms


In [22]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 871 ms, sys: 13 ms, total: 884 ms
Wall time: 874 ms


In [23]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 738 ms, sys: 10.3 ms, total: 749 ms
Wall time: 742 ms


In [24]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 817 ms, sys: 8.16 ms, total: 825 ms
Wall time: 821 ms


In [25]:
%%time
players_dict,rh = epochsG(matches[b4[0]:b4[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 810 ms, sys: 6.72 ms, total: 817 ms
Wall time: 814 ms


In [26]:
%%time
players_dict,rh = epochsG(matches[b5[0]:b5[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 864 ms, sys: 7.67 ms, total: 872 ms
Wall time: 869 ms


In [27]:
%%time
players_dict,rh = epochsG(matches[b6[0]:b6[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 762 ms, sys: 7.56 ms, total: 770 ms
Wall time: 765 ms


In [28]:
%%time
players_dict,rh = epochsG(matches[b7[0]:b7[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 826 ms, sys: 9.98 ms, total: 836 ms
Wall time: 829 ms


%%time

players_dict,rh = epochsG(matches[eg_batches_50[7][0]:eg_batches_50[7][1]],players_dict,365)
ratings_histories += [rh]

In [29]:
b = splitBatch(eg_batches_50[7],7); 
b0 = b[0]; b1 = b[1]; b2 = b[2]; b3 = b[3]; b4 = b[4]; b5 = b[5];
b6 = b[6]


In [30]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 887 ms, sys: 9.26 ms, total: 896 ms
Wall time: 890 ms


In [31]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 838 ms, sys: 6.58 ms, total: 844 ms
Wall time: 842 ms


In [32]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 918 ms, sys: 5.64 ms, total: 924 ms
Wall time: 922 ms


In [33]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 938 ms, sys: 14.6 ms, total: 952 ms
Wall time: 941 ms


In [34]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 971 ms, sys: 9.85 ms, total: 981 ms
Wall time: 974 ms


In [35]:
%%time
players_dict,rh = epochsG(matches[b4[0]:b4[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 844 ms, sys: 9.32 ms, total: 853 ms
Wall time: 848 ms


In [36]:
%%time
players_dict,rh = epochsG(matches[b5[0]:b5[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 949 ms, sys: 9.19 ms, total: 958 ms
Wall time: 956 ms


In [37]:
%%time
players_dict,rh = epochsG(matches[b6[0]:b6[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1 s, sys: 23.1 ms, total: 1.02 s
Wall time: 1 s


In [38]:
b = splitBatch(eg_batches_50[8],2); b0 = b[0]; b1 = b[1]
b

[(400000, 425000), (425000, 450000)]

In [39]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 2.09 s, sys: 34 ms, total: 2.13 s
Wall time: 2.11 s


In [40]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.9 s, sys: 34.7 ms, total: 1.94 s
Wall time: 1.94 s


In [41]:
b = splitBatch(eg_batches_50[9],8); b0 = b[0]; b1 = b[1]; 
b2 = b[2];b3 = b[3];b4 =b[4]; b5 = b[5]; b6 = b[6]; b7 = b[7]
b

[(450000, 456250),
 (456250, 462500),
 (462500, 468750),
 (468750, 475000),
 (475000, 481250),
 (481250, 487500),
 (487500, 493750),
 (493750, 500000)]

In [42]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 891 ms, sys: 17.1 ms, total: 908 ms
Wall time: 896 ms


In [43]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 984 ms, sys: 35 ms, total: 1.02 s
Wall time: 994 ms


In [44]:
b = splitBatch(b2,2)
b2_0 = b[0]; b2_1 = b[1];

In [45]:
%%time
players_dict,rh = epochsG(matches[b2_0[0]:b2_0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 754 ms, sys: 29.5 ms, total: 784 ms
Wall time: 768 ms


In [46]:
%%time
players_dict,rh = epochsG(matches[b2_1[0]:b2_1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 746 ms, sys: 13 ms, total: 759 ms
Wall time: 757 ms


In [47]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 898 ms, sys: 15.9 ms, total: 914 ms
Wall time: 909 ms


In [48]:
%%time
players_dict,rh = epochsG(matches[b4[0]:b4[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 823 ms, sys: 18 ms, total: 841 ms
Wall time: 836 ms


In [49]:
%%time
players_dict,rh = epochsG(matches[b5[0]:b5[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1 s, sys: 22.4 ms, total: 1.03 s
Wall time: 1.01 s


In [50]:
%%time
players_dict,rh = epochsG(matches[b6[0]:b6[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1 s, sys: 16.4 ms, total: 1.02 s
Wall time: 1.02 s


In [51]:
%%time
players_dict,rh = epochsG(matches[b7[0]:b7[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 966 ms, sys: 18.4 ms, total: 984 ms
Wall time: 981 ms


In [52]:
b = splitBatch(eg_batches_50[10],2); b0 = b[0]; b1 = b[1]
b

[(500000, 525000), (525000, 550000)]

In [53]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.78 s, sys: 25.6 ms, total: 1.81 s
Wall time: 1.81 s


In [54]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.88 s, sys: 43.8 ms, total: 1.92 s
Wall time: 1.91 s


In [55]:
b = splitBatch(eg_batches_50[11],5); b0 = b[0]; b1 = b[1];
b2 = b[2]; b3 = b[3];b4 = b[4];
b

[(550000, 560000),
 (560000, 570000),
 (570000, 580000),
 (580000, 590000),
 (590000, 600000)]

In [56]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.12 s, sys: 14.2 ms, total: 1.14 s
Wall time: 1.13 s


In [57]:
b = splitBatch(b1,2)
b1_0 = b[0]; b1_1 = b[1];

In [58]:
%%time
players_dict,rh = epochsG(matches[b1_0[0]:b1_0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 921 ms, sys: 7.65 ms, total: 929 ms
Wall time: 927 ms


In [59]:
%%time
players_dict,rh = epochsG(matches[b1_1[0]:b1_1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 862 ms, sys: 19.3 ms, total: 881 ms
Wall time: 879 ms


In [60]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.09 s, sys: 24.6 ms, total: 1.11 s
Wall time: 1.11 s


In [61]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.12 s, sys: 22.8 ms, total: 1.14 s
Wall time: 1.14 s


In [62]:
%%time
players_dict,rh = epochsG(matches[b4[0]:b4[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.16 s, sys: 18.9 ms, total: 1.18 s
Wall time: 1.17 s


In [63]:
%%time
players_dict,rh = epochsG(matches[eg_batches_50[12][0]:eg_batches_50[12][1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 3.54 s, sys: 16.9 ms, total: 3.56 s
Wall time: 3.56 s


In [64]:
%%time
players_dict,rh = epochsG(matches[eg_batches_50[13][0]:eg_batches_50[13][1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 3.57 s, sys: 23 ms, total: 3.59 s
Wall time: 3.59 s


In [65]:
b = splitBatch(eg_batches_50[14],2); b0 = b[0]; b1 = b[1]
b

[(700000, 725000), (725000, 750000)]

In [66]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.71 s, sys: 17.9 ms, total: 1.73 s
Wall time: 1.73 s


In [67]:
b_1 = splitBatch(b1,2)
b_10=b_1[0];b_11=b_1[1]

In [68]:
%%time
players_dict,rh = epochsG(matches[b_10[0]:b_10[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.3 s, sys: 25.1 ms, total: 1.33 s
Wall time: 1.32 s


In [69]:
%%time
players_dict,rh = epochsG(matches[b_11[0]:b_11[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.28 s, sys: 27.5 ms, total: 1.31 s
Wall time: 1.3 s


In [70]:
b = splitBatch(eg_batches_50[14],2); b0 = b[0]; b1 = b[1]
b

[(700000, 725000), (725000, 750000)]

In [71]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.71 s, sys: 18.9 ms, total: 1.73 s
Wall time: 1.73 s


In [72]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.84 s, sys: 27.6 ms, total: 1.87 s
Wall time: 1.87 s


In [73]:
b = splitBatch(eg_batches_50[15],4); b0 = b[0]; b1 = b[1];
b2 = b[2]; b3 = b[3]


In [74]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.23 s, sys: 15.2 ms, total: 1.24 s
Wall time: 1.24 s


In [75]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.31 s, sys: 27.3 ms, total: 1.34 s
Wall time: 1.33 s


In [76]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.29 s, sys: 20.4 ms, total: 1.31 s
Wall time: 1.31 s


In [77]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.07 s, sys: 15.7 ms, total: 1.09 s
Wall time: 1.08 s


In [78]:
%%time
players_dict,rh = epochsG(matches[eg_batches_50[16][0]:eg_batches_50[16][1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 3.66 s, sys: 36.4 ms, total: 3.69 s
Wall time: 3.69 s


In [79]:
b = splitBatch(eg_batches_50[17],4)
b0 = b[0]; b1 = b[1]
b

[(850000, 856745), (856745, 863490), (863490, 870235), (870235, 876979)]

In [80]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 841 ms, sys: 15.4 ms, total: 856 ms
Wall time: 852 ms


In [81]:
matches[b0[0]:b0[1]]

tourney_date  winner_id  loser_id               tourney_id
850000   2022-02-07     202400    202260  2022-M-ITF-GBR-04A-2022
850001   2022-02-07     202400    207784  2022-M-ITF-GBR-04A-2022
850002   2022-02-07     202260    208316  2022-M-ITF-GBR-04A-2022
850003   2022-02-07     105899    105181  2022-M-ITF-TUR-05A-2022
850004   2022-02-07     210472    208300  2022-M-ITF-GBR-04A-2022
...             ...        ...       ...                      ...
856740   2022-05-09     133975    109699                2022-0460
856741   2022-05-09     200484    200095                2022-0460
856742   2022-05-09     106310    105430                2022-0460
856743   2022-05-09     105181    111576                2022-0460
856744   2022-05-09     207797    106216                2022-0460

[6745 rows x 4 columns]

In [82]:
b = splitBatch(eg_batches_50[17],4)
b0 = b[0]; b1 = b[1]; b2 = b[2]; b3 = b[3];
b

[(850000, 856745), (856745, 863490), (863490, 870235), (870235, 876979)]

In [83]:
%%time
players_dict,rh = epochsG(matches[b0[0]:b0[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 837 ms, sys: 14.2 ms, total: 851 ms
Wall time: 849 ms


In [84]:
%%time
players_dict,rh = epochsG(matches[b1[0]:b1[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 990 ms, sys: 22.5 ms, total: 1.01 s
Wall time: 1.01 s


In [85]:
%%time
players_dict,rh = epochsG(matches[b2[0]:b2[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 1.04 s, sys: 20.1 ms, total: 1.06 s
Wall time: 1.05 s


In [86]:
%%time
players_dict,rh = epochsG(matches[b3[0]:b3[1]],players_dict,365)
ratings_histories += [rh]

CPU times: user 990 ms, sys: 13.6 ms, total: 1 s
Wall time: 998 ms


In [87]:
ratings_histories

[{(113987, Timestamp('1878-07-09 00:00:00')): (1753.3297594262692,
   181.34879738199115),
  (113963, Timestamp('1878-07-09 00:00:00')): (1572.1294502951291,
   193.53427121852724),
  (113999, Timestamp('1878-07-09 00:00:00')): (1667.529087702264,
   208.56031981663227),
  (114158, Timestamp('1878-07-09 00:00:00')): (1599.8752635134226,
   227.73539746084663),
  (114149, Timestamp('1878-07-09 00:00:00')): (1599.8752635134226,
   227.73539746084663),
  (113953, Timestamp('1878-07-09 00:00:00')): (1731.8366983918638,
   155.16996412112348),
  (113976, Timestamp('1878-07-09 00:00:00')): (1400.1247364865774,
   227.73539746084663),
  (114154, Timestamp('1878-07-09 00:00:00')): (1500.0, 253.4045963894164),
  (114152, Timestamp('1878-07-09 00:00:00')): (1500.0, 253.4045963894164),
  (114147, Timestamp('1878-07-09 00:00:00')): (1500.0, 253.4045963894164),
  (114146, Timestamp('1878-07-09 00:00:00')): (1500.0, 253.4045963894164),
  (113979, Timestamp('1878-07-09 00:00:00')): (1599.875263513422